In [ ]:
# Imports and config

import math
import networkx as nx
import matplotlib.pyplot as plt
import re
import ast
import mpld3

import plotly
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.widgets import GraphWidget
#from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
from ipywidgets.embed import embed_minimal_html

plotly.tools.set_credentials_file(username='jdonas', api_key='l0A7xfAuvUL9X3QAIjbK')

%matplotlib inline
plt.rcParams['figure.figsize'] = [10, 10]

In [ ]:
# Helper functions

def nodeDistance(n1, n2):
    x1 = n1[0]
    y1 = n1[1]
    x2 = n2[0]
    y2 = n2[1]
    
    return math.sqrt((x2 - x1)**2 + (y2 - y1)**2)

def matchLine(line):
    match = re.match( r'^(.*)\|(.*)$', line)
    left = match.group(1)
    right = match.group(2)
    coords = ast.literal_eval(left)
    coords = (coords[1], -coords[0])
    return (left, coords, right)

def createGraphFromFile(filePath):
    G = nx.Graph()
    
    # Open the file and start reading line by line
    with open(filePath) as fp:  
        line = fp.readline()
        
        while line:
            # Skip the file header and/or empty lines
            if line[0] != "(":
                line = fp.readline()
                continue
                
            # Match the line to a regex to extract node data
            (parentNode, parentNodeCoords, numEdges) = matchLine(line)
            if int(numEdges) != 0:
                G.add_node(parentNode, pos=parentNodeCoords)
                
            # Add edges to the graph
            for i in range(int(numEdges)):
                line = fp.readline()
                (edgeNode, edgeNodeCoords, meta) = matchLine(line)
                G.add_node(edgeNode, pos=edgeNodeCoords)
                G.add_edge(parentNode, edgeNode, distance=nodeDistance(parentNodeCoords, edgeNodeCoords))
            
            line = fp.readline()
    
    return G

In [ ]:
G = createGraphFromFile("mapOutputs/a_junius_fullres_black-and-white_#2_23h41m54s/Graph Detection_guo_hall_graph_detection_fullres_black-and-white.txt")

edge_trace = go.Scatter(
    x=[],
    y=[],
    line=dict(width=1,color='#888'),
    hoverinfo='none',
    mode='lines')

for edge in G.edges():
    x0, y0 = G.node[edge[0]]['pos']
    x1, y1 = G.node[edge[1]]['pos']
    edge_trace['x'] += tuple([x0, x1, None])
    edge_trace['y'] += tuple([y0, y1, None])

node_trace = go.Scatter(
    x=[],
    y=[],
    text=[],
    mode='markers',
    hoverinfo='text',
    marker=dict(
        color=['black'] * len(G),
        size=[5] * len(G)))

for node in G.nodes():
    x, y = G.node[node]['pos']
    node_trace['x'] += tuple([x])
    node_trace['y'] += tuple([y])
    node_trace['text'] += tuple([node])

fig = go.Figure(data=[edge_trace, node_trace],
                layout=go.Layout(
                height=800,
                width=800,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20,l=5,r=5,t=40),
                xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))




f = go.FigureWidget(data=[edge_trace, node_trace],
                    layout=go.Layout(
                    height=800,
                    width=800,
                    showlegend=False,
                    hovermode='closest',
                    margin=dict(b=20,l=5,r=5,t=40),
                    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

scatter = f.data[1]

# create our callback function
def update_point(trace, points, selector):
    c = list(scatter.marker.color)
    s = list(scatter.marker.size)
    for i in points.point_inds:
        c[i] = '#bae2be'
        s[i] = 20
        scatter.marker.color = c
        scatter.marker.size = s


scatter.on_click(update_point)
print(type(f))
f
#py.plot(f, filename='DH')
#iplot(f)

In [ ]:
def Test(event):
    print(test)
    # Arbitrary start and end coordinates
    #startCoordinates = "(2, 3)"
    #endCoordinates = "(229, 313)"
    startCoordinates = "(1464, 2969)"
    endCoordinates = "(7345, 2642)"


    # Get path using Dijkstra's algorithm
    path = nx.dijkstra_path(G, startCoordinates, endCoordinates, 'distance')

    # Get edges, colors, and positions of shortest path nodes
    pos = {}
    edges = []
    colorMap = []
    sizeMap = []
    for i, val in enumerate(path):
        pos[val] = G.node[val]['pos']

        if i+1 < len(path):
            edges.append((path[i], path[i+1]))
        if i == 0 or i == len(path)-1:
            colorMap.append("blue")
            sizeMap.append(200)
        else:
            colorMap.append("red")
            sizeMap.append(100)

    # Draw the shortest path
    nx.draw_networkx_nodes(G, pos, nodelist=path, node_color=colorMap, node_size=sizeMap)
    nx.draw_networkx_edges(G, pos, edgelist=edges, edge_color='r', width=5); # semicolon to suppress output

# Draw underlying graph
#G = createGraphFromFile("mapOutputs/TestMap.txt")
G = createGraphFromFile("mapOutputs/a_junius_fullres_black-and-white_#2_23h41m54s/Graph Detection_guo_hall_graph_detection_fullres_black-and-white.txt")
#nx.draw(G, nx.get_node_attributes(G, 'pos'), node_size=10, node_color="black", with_labels=True, font_size=7)
#nx.draw(G, nx.get_node_attributes(G, 'pos'), node_size=10, node_color="black")


fig, ax = plt.subplots(figsize=(13,13))
scatter = nx.draw_networkx_nodes(G, nx.get_node_attributes(G, 'pos'), node_size=15, node_color="black")
nx.draw_networkx_edges(G, nx.get_node_attributes(G, 'pos'))
fig.canvas.mpl_connect('button_press_event', Test)

labels = list(G.nodes())
tooltip = mpld3.plugins.PointLabelTooltip(scatter, labels=labels)
mpld3.plugins.connect(fig, tooltip)

mpld3.show()